In [1]:
import sys
import codecs

### Challege 1
#### Convert Hex to Base64
Test string: 49276d206b696c6c696e6720796f757220627261696e206c696b65206120706f69736f6e6f7573206d757368726f6f6d

Ouput: SSdtIGtpbGxpbmcgeW91ciBicmFpbiBsaWtlIGEgcG9pc29ub3VzIG11c2hyb29t

In [2]:
def HexToB64(bytes_Hex):
    hex_Decoded = codecs.decode(bytes_Hex, 'hex')
    b64_Encoded = codecs.encode(hex_Decoded, 'base64')
    return b64_Encoded

In [3]:
bstr_test = b'49276d206b696c6c696e6720796f757220627261696e206c696b65206120706f69736f6e6f7573206d757368726f6f6d'
print(HexToB64(bstr_test))

b'SSdtIGtpbGxpbmcgeW91ciBicmFpbiBsaWtlIGEgcG9pc29ub3VzIG11c2hyb29t\n'


### Challege 2
#### Fixed XOR
Write a function that takes two equal-length buffers and produces their XOR combination.

If your function works properly, then when you feed it the string:

1c0111001f010100061a024b53535009181c
... after hex decoding, and when XOR'd against:

686974207468652062756c6c277320657965
... should produce:

746865206b696420646f6e277420706c6179


In [4]:
def FixedXOR(byte_str1, byte_str2):
    hex_str1 = int(str(byte_str1.decode('utf-8')), base=16)
    hex_str2 = int(str(byte_str2.decode('utf-8')), base=16)
    val_XOR = hex(hex_str1 ^ hex_str2).encode()[2:]
    return val_XOR

In [5]:
byte_teststr1 = b'1c0111001f010100061a024b53535009181c'
byte_teststr2 = b'686974207468652062756c6c277320657965'
print(FixedXOR(byte_teststr1, byte_teststr2))

b'746865206b696420646f6e277420706c6179'


### Challege 3
#### Single-byte XOR Cypher

The hex encoded string:

1b37373331363f78151b7f2b783431333d78397828372d363c78373e783a393b3736
... has been XOR'd against a single character. Find the key, decrypt the message.

You can do this by hand. But don't: write code to do it for you.

In [186]:
def GetStringLetterFreq(str_Test, dict_EnglishLetterFreq):
    """
    Input: string of letters, a dictionary containing the letters to be tested as keys
    Output: a dictionary of the frequency of letters in the string
    Notes: Called by EnglishScore
    """
    list_EnglishLetters = [i for i, k in dict_EnglishLetterFreq.items()]
    dict_StringLetterCount = dict.fromkeys(list_EnglishLetters , 0)
    str_FromBytes = ''.join([chr(b) for b in str_Test.lower()])
    str_Test = str_FromBytes
    print(str_Test)
    val_NotLetterPenalty = 0
    for c in str_Test:
        if c in list_EnglishLetters:
            dict_StringLetterCount[c] += 1
        elif c == ' ':
            val_NotLetterPenalty += 0 #no penalty for spaces
        else:
            val_NotLetterPenalty += 0.1 #adjustable penalty for non-English letter, non-space characters
    dict_StringLetterFreq = {k: v / len(str_Test) for k, v in dict_StringLetterCount.items()}
    return dict_StringLetterFreq, val_NotLetterPenalty

def EnglishScore(str_Test):
    dict_EnglishLetterFreq = {'a': 0.0817,'b': 0.0149,'c': 0.0278,'d': 0.0425,'e': 0.127,'f': 0.0223,'g': 0.0202,
                              'h': 0.0609,'i': 0.0697,'j': 0.0015,'k': 0.0077,'l': 0.0403,'m': 0.0241,'n': 0.0675,
                              'o': 0.0751,'p': 0.0193,'q': 0.001,'r': 0.0599,'s': 0.0633,'t': 0.0906,'u': 0.0276,
                              'v': 0.0098,'w': 0.0236,'x': 0.0015, 'y': 0.0197,'z': 0.0007}
    dict_TestLetterFreq, val_NotLetterPenalty = GetStringLetterFreq(str_Test, dict_EnglishLetterFreq)
    list_EnglishScore = [(a - b)**2 for (a,b) in zip(dict_TestLetterFreq.values(), dict_EnglishLetterFreq.values())]
    total_EnglishScore = sum(list_EnglishScore) + val_NotLetterPenalty
    return total_EnglishScore

def ScoreStringList(list_TestStrings):
    dict_StringScores = dict.fromkeys(list_TestStrings, 0)
    for s in list_TestStrings:
        dict_StringScores[s] = EnglishScore(s)
    string_MinScore = min(dict_StringScores, key=lambda key: dict_StringScores[key])
    return string_MinScore, dict_StringScores[string_MinScore], dict_StringScores

def SingleByteXOR(str_Encoded, byte_Char):
    hex_SingleChar = int(str(byte_Char.decode('latin-1')), base=16)
    list_Decoded = []
    for c in codecs.decode(str_Encoded, 'hex'):
        hex_CharEncoded = int(hex(c), base=16)
        val_XOR = str(hex(hex_CharEncoded ^ hex_SingleChar)[2:])
        list_Decoded.append(val_XOR)
    str_Decoded = ''.join(list_Decoded)
    try:
        str_UniDecoded = codecs.decode(str_Decoded, 'hex').decode('latin-1')
    except:
        str_UniDecoded = ''
    return str_UniDecoded

def SingleByteXORAlt(str_Encoded, byte_Char):
    str_XORd = b''
    for c in str_Encoded:
        str_XORd += bytes([c^byte_Char])
    return str_XORd

In [187]:
def DecodeSingleByteXOR(str_HexEncode):
    list_DecodedStrings = []
    for i in range(0, 256):
        test_Byte = i#codecs.encode(chr(i).encode(), 'hex')
        bytes_XORd = SingleByteXORAlt(str_HexEncode, test_Byte)
        if len(bytes_XORd) > 0:
            list_DecodedStrings.append(bytes_XORd)
    return list_DecodedStrings

In [188]:
str_SingleByteEncode = b'1b37373331363f78151b7f2b783431333d78397828372d363c78373e783a393b3736'
list_DecodedStrings = DecodeSingleByteXOR(str_SingleByteEncode)
str_BestEngScore, val_BestEngScore, dict_AllScores = ScoreStringList(list_DecodedStrings)
print(str_BestEngScore)

1b37373331363f78151b7f2b783431333d78397828372d363c78373e783a393b3736
0c26262220272g69040c6g3c692520222e69286939263e272b69262d692`282c2627
3`15151113141d5:373`5d0`5:1613111f5:1;5:0:150f141a5:151g5:1c1;1`1514
2a04040002050e4;262a4e1a4;0702000g4;0:4;1;041g050`4;040f4;0b0:0a0405
5f73737775727b3<515f3b6f3<7075777`3<7=3<6<736`727g3<737a3<7e7=7f7372
4g62626664636c2=404g2c7g2=6164666a2=6<2=7=627a636f2=626`2=6d6<6g6263
7d51515557505`1>737d1`4d1>5257555b1>5?1>4>514b505e1>515c1>5g5?5d5150
6e40404446414a0?626e0a5e0?4346444c0?4>0?5?405c414d0?404b0?4f4>4e4041
9j;?;?;;;9;>;n?09=9j?n:j?0;<;9;;;l?0;1?0:0;?:l;>;k?0;?;m?0;i;1;j;?;>
8k:>:>:::8:?:o>18<8k>o;k>1:=:8:::m>1:0>1;1:>;m:?:j>1:>:l>1:h:0:k:>:?
;h9=9=999;9<9l=2;?;h=l8h=29>9;999n=293=2829=8n9<9i=29=9o=29k939h9=9<
:i8<8<888:8=8m<3:>:i<m9i<38?8:888o<382<3938<9o8=8h<38<8n<38j828i8<8=
=n?;?;???=?:?j;4=9=n;j>n;4?8?=???h;4?5;4>4?;>h?:?o;4?;?i;4?m?5?n?;?:
<o>:>:>>><>;>k:5<8<o:k?o:5>9><>>>i:5>4:5?5>:?i>;>n:5>:>h:5>l>4>o>:>;
?l=9=9===?=8=h96?;?l9h<l96=:=?===j

In [130]:
list_DecodedStrings

[b'1b37373331363f78151b7f2b783431333d78397828372d363c78373e783a393b3736',
 b'0c26262220272g69040c6g3c692520222e69286939263e272b69262d692`282c2627',
 b'3`15151113141d5:373`5d0`5:1613111f5:1;5:0:150f141a5:151g5:1c1;1`1514',
 b'2a04040002050e4;262a4e1a4;0702000g4;0:4;1;041g050`4;040f4;0b0:0a0405',
 b'5f73737775727b3<515f3b6f3<7075777`3<7=3<6<736`727g3<737a3<7e7=7f7372',
 b'4g62626664636c2=404g2c7g2=6164666a2=6<2=7=627a636f2=626`2=6d6<6g6263',
 b'7d51515557505`1>737d1`4d1>5257555b1>5?1>4>514b505e1>515c1>5g5?5d5150',
 b'6e40404446414a0?626e0a5e0?4346444c0?4>0?5?405c414d0?404b0?4f4>4e4041',
 b'9j;?;?;;;9;>;n?09=9j?n:j?0;<;9;;;l?0;1?0:0;?:l;>;k?0;?;m?0;i;1;j;?;>',
 b'8k:>:>:::8:?:o>18<8k>o;k>1:=:8:::m>1:0>1;1:>;m:?:j>1:>:l>1:h:0:k:>:?',
 b';h9=9=999;9<9l=2;?;h=l8h=29>9;999n=293=2829=8n9<9i=29=9o=29k939h9=9<',
 b':i8<8<888:8=8m<3:>:i<m9i<38?8:888o<382<3938<9o8=8h<38<8n<38j828i8<8=',
 b'=n?;?;???=?:?j;4=9=n;j>n;4?8?=???h;4?5;4>4?;>h?:?o;4?;?i;4?m?5?n?;?:',
 b'<o>:>:>>><>;>k:5<8<o:k?o:5>9><>>>i:

### Challenge 4
#### Detect single-character XOR
One of the 60-character strings in this file has been encrypted by single-character XOR.

In [172]:
f = open('./ChallengeSet1_4.txt', 'rb')
list_EncodedStrings = [l.strip() for l in f]

In [173]:
list_EncodedStrings

[b'...']

In [174]:
list_AllDecodedStrings = []
for s in list_EncodedStrings:
    list_DecodedElement = DecodeSingleByteXOR(s)
    if len(list_DecodedElement) > 0:
        str_BestEngScore, val_BestEngScore, dict_AllScores = ScoreStringList(list_DecodedElement)
        print(str_BestEngScore)
        list_AllDecodedStrings.extend(list_DecodedElement)


b'0e3647e8592d35514a081243582536ed3de6734059001e3f535ce6271032'
b'1d2756d9483e24405`190352493427de2ed7625148110d2g424bd7360123'
b'2g1465g:7;0f17736c2:30617:0714gf1fg451627;223g1d717ag4053210'
b'3f0574f;6:1g06627b3;21706;1605fg0gf540736:332f0e606`f5142301'
b'4a7203a<1=6`71150e4<56071<6172a`7`a237041=445a7b171ga2635476'
b'5`6312`=0<7a60041d5=47160=7063`a6a`326150<554`6c060f`3724567'
b'6c5021c>3?4b53372g6>74253>4350cb5bc015263?667c5`353ec0417654'
b'7b4130b?2>5c42263f7?65342?5241bc4cb104372>776b4a242db1506745'
b'8m;><?m0=1:l;==9<i809:<;=0:=;>ml;lm>?;<8=1889m;n=;=km>:?98;:'
b'9l:?=>l1<0;m:<<8=h918;=:<1;<:?lm:ml?>:=9<0998l:o<:<jl?;>89:;'
b':o9<>=o2?38n9??;>k:2;8>9?28?9<on9no<=9>:?3::;o9l?9?io<8=;:98'
b';n8=?<n3>29o8>>:?j;3:9?8>39>8=no8on=<8?;>2;;:n8m>8>hn=9<:;89'
b'<i?:8;i495>h?99=8m<4=>8?94>9?:ih?hi:;?8<95<<=i?j9?9oi:>;=<?>'
b'=h>;9:h584?i>88<9l=5<?9>85?8>;hi>ih;:>9=84==<h>k8>8nh;?:<=>?'
b'>k=8:9k6;7<j=;;?:o>6?<:=;6<;=8kj=jk89=:>;7>>?k=h;=;mk8<9?>=<'
b'?j<9;8j7:6=k<::>;n?7>=;<:7=:<9jk<kj98<

b'Y\nZYY\x0bZ\\\\\n[Y\\XZ^Z\x08Y\\XQ\\X\x0c\x0cX\\]\x08Y[Z^[Z]X]\nY[Z\x08YQX^X\x0cX\x0b]\x0fX^\\P\\\x0c'
b'Z\tYZZ\x08Y__\tXZ_[Y]Y\x0bZ_[R_[\x0f\x0f[_^\x0bZXY]XY^[^\tZXY\x0bZR[][\x0f[\x08^\x0c[]_S_\x0f'
b'[\x08X[[\tX^^\x08Y[^ZX\\X\n[^ZS^Z\x0e\x0eZ^_\n[YX\\YX_Z_\x08[YX\n[SZ\\Z\x0eZ\t_\rZ\\^R^\x0e'
b'\\\x0f_\\\\\x0e_YY\x0f^\\Y]_[_\r\\Y]TY]\t\t]YX\r\\^_[^_X]X\x0f\\^_\r\\T][]\t]\x0eX\n][YUY\t'
b']\x0e^]]\x0f^XX\x0e_]X\\^Z^\x0c]X\\UX\\\x08\x08\\XY\x0c]_^Z_^Y\\Y\x0e]_^\x0c]U\\Z\\\x08\\\x0fY\x0b\\ZXTX\x08'
b'^\r]^^\x0c][[\r\\^[_]Y]\x0f^[_V[_\x0b\x0b_[Z\x0f^\\]Y\\]Z_Z\r^\\]\x0f^V_Y_\x0b_\x0cZ\x08_Y[W[\x0b'
b'_\x0c\\__\r\\ZZ\x0c]_Z^\\X\\\x0e_Z^WZ^\n\n^Z[\x0e_]\\X]\\[^[\x0c_]\\\x0e_W^X^\n^\r[\t^XZVZ\n'
b'@\x13C@@\x12CEE\x13B@EACGC\x11@EAHEA\x15\x15AED\x11@BCGBCDAD\x13@BC\x11@HAGA\x15A\x12D\x16AGEIE\x15'
b'A\x12BAA\x13BDD\x12CAD@BFB\x10AD@ID@\x14\x14@DE\x10ACBFCBE@E\x12ACB\x10AI@F@\x14@\x13E\x17@FDHD\x14'
b'B\x11ABB\x10AGG\x11@BGCAEA\x13BGCJGC\x17\x17CGF\x13B@AE@AFCF\x11B@A\x13BJCEC\x17C\x10F\x14C

b'\x00\x01\x01P\x02\x00\x05\t\x01\t\x01W\x03\x03\x06WT\x07\x01P\x00\x02\x03W\x01R\x00\x01\x00\x06\x05WT\x02W\x07\x02U\x00P\x04U\x02\tTS\x05\x00\x05RP\tT\t\x03W\x03S\x01\x04'
b'\x03\x02\x02S\x01\x03\x06\n\x02\n\x02T\x00\x00\x05TW\x04\x02S\x03\x01\x00T\x02Q\x03\x02\x03\x05\x06TW\x01T\x04\x01V\x03S\x07V\x01\nWP\x06\x03\x06QS\nW\n\x00T\x00P\x02\x07'
b'\x02\x03\x03R\x00\x02\x07\x0b\x03\x0b\x03U\x01\x01\x04UV\x05\x03R\x02\x00\x01U\x03P\x02\x03\x02\x04\x07UV\x00U\x05\x00W\x02R\x06W\x00\x0bVQ\x07\x02\x07PR\x0bV\x0b\x01U\x01Q\x03\x06'
b'\x05\x04\x04U\x07\x05\x00\x0c\x04\x0c\x04R\x06\x06\x03RQ\x02\x04U\x05\x07\x06R\x04W\x05\x04\x05\x03\x00RQ\x07R\x02\x07P\x05U\x01P\x07\x0cQV\x00\x05\x00WU\x0cQ\x0c\x06R\x06V\x04\x01'
b'\x04\x05\x05T\x06\x04\x01\r\x05\r\x05S\x07\x07\x02SP\x03\x05T\x04\x06\x07S\x05V\x04\x05\x04\x02\x01SP\x06S\x03\x06Q\x04T\x00Q\x06\rPW\x01\x04\x01VT\rP\r\x07S\x07W\x05\x00'
b'\x07\x06\x06W\x05\x07\x02\x0e\x06\x0e\x06P\x04\x04\x01PS\x00\x06W\x07\x05\x04P\x06U\x07\x06\x07\x01\x02PS\x0

b'!putvwwstttwtwpqv%u!v"v&v}p}w"qp! q%tws&w!t|wuu&rvq\'" ttqtt}'
b" qtuwvvruuuvuvqpw$t w#w'w|q|v#pq !p$uvr'v u}vtt'swp&#!uupuu|"
b'#rwvtuuqvvvuvurst\'w#t t$t\x7fr\x7fu sr#"s\'vuq$u#v~uww$pts% "vvsvv\x7f'
b'"svwuttpwwwtwtsru&v"u!u%u~s~t!rs"#r&wtp%t"w\x7ftvv%qur$!#wwrww~'
b'-|yxz{{\x7fxxx{x{|}z)y-z.z*zq|q{.}|-,})x{\x7f*{-xp{yy*~z}+.,xx}xxq'
b',}xy{zz~yyyzyz}|{(x,{/{+{p}pz/|},-|(yz~+z,yqzxx+\x7f{|*/-yy|yyp'
b'/~{zxyy}zzzyzy~\x7fx+{/x,x(xs~sy,\x7f~/.\x7f+zy}(y/zry{{(|x\x7f),.zz\x7fzzs'
b'.\x7fz{yxx|{{{x{x\x7f~y*z.y-y)yr\x7frx-~\x7f./~*{x|)x.{sxzz)}y~(-/{{~{{r'
b')x}|~\x7f\x7f{|||\x7f|\x7fxy~-})~*~.~uxu\x7f*yx)(y-|\x7f{.\x7f)|t\x7f}}.z~y/*(||y||u'
b'(y|}\x7f~~z}}}~}~yx\x7f,|(\x7f+\x7f/\x7ftyt~+xy()x,}~z/~(}u~||/{\x7fx.+)}}x}}t'
b'+z\x7f~|}}y~~~}~}z{|/\x7f+|(|,|wzw}({z+*{/~}y,}+~v}\x7f\x7f,x|{-(*~~{~~w'
b'*{~\x7f}||x\x7f\x7f\x7f|\x7f|{z}.~*})}-}v{v|)z{*+z.\x7f|x-|*\x7fw|~~-y}z,)+\x7f\x7fz\x7f\x7fv'
b'5da`bccg```c`cdeb1a5b6b2bidic6ed54e1`cg2c5`hcaa2fbe364``e``i'
b'4e`acbbfaaababedc0`4c7c3cheh

b'\xb4\xb4\xb5\xe0\xe1\xb4\xb0\xb5\xb7\xe1\xb5\xb3\xb0\xe1\xb5\xbc\xb5\xbd\xb6\xe7\xb4\xb2\xb5\xe1\xb0\xe6\xb7\xe0\xb5\xe6\xb1\xb2\xb6\xb2\xe2\xbd\xb4\xe1\xb7\xe1\xb5\xb0\xb6\xbd\xb1\xb0\xb0\xe5\xb6\xb4\xe1\xe1\xb5\xb1\xb4\xe0\xb4\xe7\xb6\xb4'
b'\xb5\xb5\xb4\xe1\xe0\xb5\xb1\xb4\xb6\xe0\xb4\xb2\xb1\xe0\xb4\xbd\xb4\xbc\xb7\xe6\xb5\xb3\xb4\xe0\xb1\xe7\xb6\xe1\xb4\xe7\xb0\xb3\xb7\xb3\xe3\xbc\xb5\xe0\xb6\xe0\xb4\xb1\xb7\xbc\xb0\xb1\xb1\xe4\xb7\xb5\xe0\xe0\xb4\xb0\xb5\xe1\xb5\xe6\xb7\xb5'
b'\xb6\xb6\xb7\xe2\xe3\xb6\xb2\xb7\xb5\xe3\xb7\xb1\xb2\xe3\xb7\xbe\xb7\xbf\xb4\xe5\xb6\xb0\xb7\xe3\xb2\xe4\xb5\xe2\xb7\xe4\xb3\xb0\xb4\xb0\xe0\xbf\xb6\xe3\xb5\xe3\xb7\xb2\xb4\xbf\xb3\xb2\xb2\xe7\xb4\xb6\xe3\xe3\xb7\xb3\xb6\xe2\xb6\xe5\xb4\xb6'
b'\xb7\xb7\xb6\xe3\xe2\xb7\xb3\xb6\xb4\xe2\xb6\xb0\xb3\xe2\xb6\xbf\xb6\xbe\xb5\xe4\xb7\xb1\xb6\xe2\xb3\xe5\xb4\xe3\xb6\xe5\xb2\xb1\xb5\xb1\xe1\xbe\xb7\xe2\xb4\xe2\xb6\xb3\xb5\xbe\xb2\xb3\xb3\xe6\xb5\xb7\xe2\xe2\xb6\xb2\xb7\xe3\xb7\xe4\xb5\xb7'
b'\xb8\xb8\xb9\xec\xed\x

...

b'2d5801ee2654113e2da00b58e9260d643c10423e1d1f42093b0d0f7d5102'
b'3649211f210456051e290f1b4c584d0749220c280b2a50531f262901503e'
b'2758300g301547140d381g0c5b495e1658331b391c3`41420g373810412d'
b'146;033d032674273g0;2d3`6a7:6f256;002a0:2`0c72713d040;23721g'
b'057:122e123765362f1:3e2a7`6;7g347:113`1;3a1b63602e151:32630f'
b'720=655b654012415a6=4b5f0g1<0`430=664g6<4f6e14175b626=45147a'
b'631<744c745103504`7<5c4g1f0=1a521<775f7=5g7d05064c737<54056`'
b'502?477`476230637c4?6`7d2e3>2b612?446e4>6d4g36357`404?67365c'
b'413>566a567321726b5>7a6e3d2?3c703>557d5?7e5f27246a515>76274b'
b';><1:99n:98<=>8=9m:18n9j<k=0<l8?<1::8k:08j:i=8=;9n:>:189=8;m'
b':?=0;88o;89=<?9<8l;09o8k=j<1=m9>=0;;9j;19k;h<9<:8o;?;098<9:l'
b'9<>38;;l8;:>?<:?;o83:l;h>i?2>n:=>388:i82:h8k?:?9;l8<83:;?:9o'
b'8=?29::m9:;?>=;>:n92;m:i?h>3?o;<?299;h93;i9j>;>8:m9=92;:>;8n'
b'?:85>==j>=<89:<9=i>5<j=n8o948h<;85>><o>4<n>m9<9?=j>:>5<=9<?i'
b'>;94?<<k?<=98;=8<h?4=k<o9n859i=:94??=n?5=o?l8=8><k?;?4=<8=>h'
b'=8:7<??h<?>:;8>;?k<7>h?l:m;6:j>9:7<<>m

b'3f21060de62c052a17576e2ce729242b3e3621300627f01e52580a480050'
b'1b381a11351f4f5d22040c3c4b3e7d263714e8e61a571d107a34260a4a51'
b'0c290`00240g5g4e33151b2b5c2d6e372605d9d70`460e016`25371`5`40'
b'3`1:3c33173d6d7f00262a1a6`1g5f041536g:g43c753f325c16042c6c73'
b'2a0;2b22062e7e6g11373`0`7a0f4g150427f;f52b642g234b07153b7b62'
b'5f7<5e55715b0b1`66404g7g0f7a3`627350a<a25e135`543e70624e0e15'
b'4g6=4d44604c1c0a77515f6f1g6`2a736241`=`34d024a452d61735d1d04'
b'7d5>7g77537`2`3b44626e5e2d5c1b405172c>c07g317b761g52406g2g37'
b'6e4?6f66426a3a2c55737d4d3e4b0c514063b?b16f206c670f43517f3f26'
b'9j;09i99;=9n<n=l::8<8k;k<j;m?l:>;?9<m0m>9i=?9l98?i;<:>8i<i=9'
b'8k:18h88:<8o=o<m;;9=9j:j=k:l>m;?:>8=l1l?8h<>8m89>h:=;?9h=h<8'
b';h92;k;;9?;l>l?n88:>:i9i>h9o=n8<9=;>o2o<;k?=;n;:=k9>8<:k>k?;'
b':i83:j::8>:m?m>o99;?;h8h?i8n<o9=8<:?n3n=:j><:o:;<j8?9=;j?j>:'
b'=n?4=m==?9=j8j9h>><8<o?o8n?i;h>:?;=8i4i:=m9;=h=<;m?8>:<m8m9='
b'<o>5<l<<>8<k9k8i??=9=n>n9o>h:i?;>:<9h5h;<l8:<i<=:l>9?;=l9l8<'
b'?l=6?o??=;?h:h;j<<>:>m=m:l=k9j<8=9?:k6

b'36053935f051f959093252411e2d5af81f360c0fa15d0b373b1d26323b77'
b'501424184202206215e05944505c4817514540445b0207025de05b050932'
b'410535095313317304d14855414b5906405451554c1316134ed14c141823'
b'7236063:6020024037g27;66727a6:35736762667`2025207fg27`272;10'
b'6327172;7131135126f36:77636`7;24627673776a3134316gf36a363:01'
b'1450605<0646642651a41=00141g0<53150104001f4643461`a41f414=76'
b'0541714=1757753740`50<11050f1=42041015110g5752570a`50g505<67'
b'3672427>2464460473c63?22363e2>71372326223d6461643bc63d636?54'
b'2763536?3575571562b72>33272d3?60263237332e7570752cb72e727>45'
b'=89<:<90<:8::8>:9=m8=1<<=8=k<09?=9<=<8<<=j8:8?8:=lm8=j8=81;:'
b'<98=;=81=;9;;9?;8<l9<0==<9<j=18><8=<=9==<k9;9>9;<ml9<k9<90:;'
b'?:;>8>;2>8:88:<8;?o:?3>>?:?i>2;=?;>?>:>>?h:8:=:8?no:?h:?:398'
b'>;:?9?:3?9;99;=9:>n;>2??>;>h?3:<>:?>?;??>i;9;<;9>on;>i;>;289'
b'9<=8>8=48><>><:>=9i<95889<9o84=;9=898<889n<><;<>9hi<9n<9<5?>'
b'8=<9?9<59?=??=;?<8h=84998=8n95<:8<989=998o=?=:=?8ih=8o=8=4>?'
b';>?:<:?6:<><<>8<?;k>;7::;>;m:6?9;?:;:>

b'\x0e\x03\x08_\tY\x0b\r\t\x0e\n]\x0e\x0e\n_\t]\x0e\x0f\x0e\n\n\n\x0b\x02\n\n^\r\x0b\x08\x0f\n\x0f\x0c\x0f\x03\nZ\x0b\x0e\n\r\r^\n]\t\x0f\nZ\x0e\x03\n\x0c\x0b\n\x0eY'
b'\t\x04\x0fX\x0e^\x0c\n\x0e\t\rZ\t\t\rX\x0eZ\t\x08\t\r\r\r\x0c\x05\r\rY\n\x0c\x0f\x08\r\x08\x0b\x08\x04\r]\x0c\t\r\n\nY\rZ\x0e\x08\r]\t\x04\r\x0b\x0c\r\t^'
b'\x08\x05\x0eY\x0f_\r\x0b\x0f\x08\x0c[\x08\x08\x0cY\x0f[\x08\t\x08\x0c\x0c\x0c\r\x04\x0c\x0cX\x0b\r\x0e\t\x0c\t\n\t\x05\x0c\\\r\x08\x0c\x0b\x0bX\x0c[\x0f\t\x0c\\\x08\x05\x0c\n\r\x0c\x08_'
b'\x0b\x06\rZ\x0c\\\x0e\x08\x0c\x0b\x0fX\x0b\x0b\x0fZ\x0cX\x0b\n\x0b\x0f\x0f\x0f\x0e\x07\x0f\x0f[\x08\x0e\r\n\x0f\n\t\n\x06\x0f_\x0e\x0b\x0f\x08\x08[\x0fX\x0c\n\x0f_\x0b\x06\x0f\t\x0e\x0f\x0b\\'
b'\n\x07\x0c[\r]\x0f\t\r\n\x0eY\n\n\x0e[\rY\n\x0b\n\x0e\x0e\x0e\x0f\x06\x0e\x0eZ\t\x0f\x0c\x0b\x0e\x0b\x08\x0b\x07\x0e^\x0f\n\x0e\t\tZ\x0eY\r\x0b\x0e^\n\x07\x0e\x08\x0f\x0e\n]'
b'uxs$r"pvruq&uuq$r&utuqqqpyqq%vpstqtwtxq!puqvv%q&rtq!uxqwpqu"'
b"tyr%s#qwstp'ttp%s'tutpppqxpp$wqrupuvuyp qtpww$p's

b'32042f46431d2c44607934ed180c1028136a5f2b26092e3b2c4e2930585a'


In [139]:
str_BestEngScore, val_BestEngScore, dict_AllScores = ScoreStringList(list_AllDecodedStrings)
print(str_BestEngScore)

b'1c3df1135321a8e9241a5607f8305d571aa546001e3254555a11511924'


In [92]:
[(k, dict_AllScores[k]) for k in sorted(dict_AllScores, key = dict_AllScores.get)]

[('iU\x1chkZHXPIK\x16tXKAnQWs\x1bAD>XtbxIK', 0.46956448222222225),
 ('Iu<HKzhxpik6TxkaNqwS;ad\x1exTBXik', 0.46956448222222225),
 ('kW\x1ejiXJZRKI\x14vZIClSUq\x19CF<Zv`zKI', 0.5918067044444444),
 ('Kw>JIxjzrki4VzicLsuQ9cf\x1czV@Zki', 0.5918067044444444),
 ('yTh\x8bebwt cAdCPZJs\x82G2fDf\x80\x11X}OAb', 0.6395844822222222),
 ('en.IomBlIKqA2Iycn\x1elqK? \\ÀqowJD', 0.6495600377777777),
 ('Ea NEy2HcAoF2Um\x7fCUxe%s)Sv69KQL', 0.7314089266666666),
 ('uNtHLuwERzQ4ngl3)&jMivT\x84gef*R\x85', 0.7346467044444444),
 ('cS\x84roywwD liGA\x95\x94\x8aKdQ+Eb#uUfn9o', 0.7348155933333332),
 ('wpUs{gnns F8b-aT2*zRAh{Gj>xuED', 0.7353911488888889),
 ('wLvJNwuGPxS6len1+$hOktV\x86egd(P\x87', 0.7408933711111111),
 ('xW"SJ<T\x86Xm\x7fECebqm$ceU&GSzndvR×', 0.7416867044444444),
 ('zU QH>V\x84Zo}GAg`so&agW$EQxlftPÕ', 0.7479355933333333),
 ('vMwKOvtFQyR7mdo0*%iNjuW\x87dfe)Q\x86', 0.7487667044444444),
 ('TbHyc\x15ZW:o\x1eJckNrh\x1e\x1ffz¡X«SVqAKF', 0.75226226),
 ('tBhYC5zw\x1aO>jCKnRH>?FZ\x81x\x8bsvQakf', 0.75226226),

In [37]:
len(dict_AllScores)

256